# Segment Anything Model for Geospatial Data

[![image](https://studiolab.sagemaker.aws/studiolab.svg)](https://studiolab.sagemaker.aws/import/github/opengeos/segment-geospatial/blob/main/docs/examples/satellite.ipynb)
[![image](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/opengeos/segment-geospatial/blob/main/docs/examples/satellite.ipynb)

This notebook shows how to use segment satellite imagery using the Segment Anything Model (SAM) with a few lines of code.

Make sure you use GPU runtime for this notebook. For Google Colab, go to `Runtime` -> `Change runtime type` and select `GPU` as the hardware accelerator.

## Install dependencies

Uncomment and run the following cell to install the required dependencies.


In [15]:
!pip install segment-geospatial
!pip install leafmap
!pip install localtileserver

## Import libraries

In [16]:
import leafmap
from samgeo import SamGeo
from samgeo.common import tms_to_geotiff

## Create an interactive map

In [17]:
# m = leafmap.Map(center=[29.676840, -95.369222], zoom=19)
m = leafmap.Map(center=[77.70498446518944, 27.47673919229822], zoom=19) # 27.4786959892737, 77.68525222155318
m.add_basemap("SATELLITE")
m

Output hidden; open in https://colab.research.google.com to view.

Pan and zoom the map to select the area of interest. Use the draw tools to draw a polygon or rectangle on the map

In [18]:
if m.user_roi_bounds() is not None:
    bbox = m.user_roi_bounds()
else:
    # bbox = [77.67948010820659, 27.474726730458432,
    #         77.69227960862014, 27.482046427372985] # [27.474726730458432, 77.67948010820659] [27.482046427372985, 77.69227960862014]
    bbox = [77.70352802580877, 27.475661205136298,
            77.70674131195618, 27.477617280005973]

bbox

[77.70352802580877, 27.475661205136298, 77.70674131195618, 27.477617280005973]

## Download map tiles

Download maps tiles and mosaic them into a single GeoTIFF file

In [19]:
image = "satellite.tif"

Besides the `satellite` basemap, you can use any of the following basemaps returned by the `get_basemaps()` function:

In [20]:
# get_basemaps().keys()

Specify the basemap as the source.

In [21]:
tms_to_geotiff(output=image, bbox=bbox, zoom=20, source="Satellite", overwrite=True)

Downloaded image 01/88
Downloaded image 02/88
Downloaded image 03/88
Downloaded image 04/88
Downloaded image 05/88
Downloaded image 06/88
Downloaded image 07/88
Downloaded image 08/88
Downloaded image 09/88
Downloaded image 10/88
Downloaded image 11/88
Downloaded image 12/88
Downloaded image 13/88
Downloaded image 14/88
Downloaded image 15/88
Downloaded image 16/88
Downloaded image 17/88
Downloaded image 18/88
Downloaded image 19/88
Downloaded image 20/88
Downloaded image 21/88
Downloaded image 22/88
Downloaded image 23/88
Downloaded image 24/88
Downloaded image 25/88
Downloaded image 26/88
Downloaded image 27/88
Downloaded image 28/88
Downloaded image 29/88
Downloaded image 30/88
Downloaded image 31/88
Downloaded image 32/88
Downloaded image 33/88
Downloaded image 34/88
Downloaded image 35/88
Downloaded image 36/88
Downloaded image 37/88
Downloaded image 38/88
Downloaded image 39/88
Downloaded image 40/88
Downloaded image 41/88
Downloaded image 42/88
Downloaded image 43/88
Downloaded 

You can also use your own image. Uncomment and run the following cell to use your own image.

In [22]:
# image = '/path/to/your/own/image.tif'

Display the downloaded image on the map.

In [23]:
m.layers[-1].visible = False  # turn off the basemap
m.add_raster(image, layer_name="Image")
m

Map(center=[27.476639, 77.7051345], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title'…

## Initialize SAM class

In [24]:
sam = SamGeo(
    model_type="vit_h",
    checkpoint="sam_vit_h_4b8939.pth",
    sam_kwargs=None,
)

## Segment the image

Set `batch=True` to segment the image in batches. This is useful for large images that cannot fit in memory.

In [25]:
mask = "segment.tif"
sam.generate(
    image, mask, batch=True, foreground=True, erosion_kernel=(3, 3), mask_multiplier=255
)

100%|██████████| 20/20 [02:32<00:00,  7.62s/it]


## Polygonize the raster data

Save the segmentation results as a GeoPackage file.

In [26]:
vector = "segment.gpkg"
sam.tiff_to_gpkg(mask, vector, simplify_tolerance=None)

You can also save the segmentation results as any vector data format supported by GeoPandas.

In [27]:
shapefile = "segment.shp"
sam.tiff_to_vector(mask, shapefile)

## Visualize the results

In [29]:
style = {
    "color": "#3388ff",
    "weight": 2,
    "fillColor": "#7c4185",
    "fillOpacity": 0.5,
}
m.add_vector(vector, layer_name="Vector", style=style)
m

Map(bottom=4877467.0, center=[77.70490492295941, 27.47735381126404], controls=(ZoomControl(options=['position'…